## 
ELEX 4653 Lab 3

This lab provides practice on writing generator functions, writing and using regular expressions, sorting, and user-defined types.

_Version 2: Corrected checking code for Question 3._

_Version 3: Added requirement in Question 4 that the sort be "stable" (order preserving)_

_Version 4: Fixed example for Question 3._

Instructions:

- Modify this notebook by adding the Python code described below.

- Test your code using the menu item `Cell  ► Run All` or `Run ► Run All Cells`

- Save the notebook (the .ipynb file) and upload it to the appropriate Assignment folder on the course web site.

#### Question 1

Write a generator function `birange(n)` that yields integers ranging from `-n` to `n` in increments of 1 where `n` is a positive, non-zero number.   For example, `list(birange(3))` would have the value `[-3, -2, -1, 0, 1, 2, 3]`.

#### Question 2

Create strings named as follows that define the regular expressions described below:

* `bcitid`: A string starting with an upper-case 'A', followed by exactly 8 digits, followed by zero or more characters.
* `amount`: A string starting with a dollar-sign, followed by one or more digits, followed by a period, followed by and ending with two digits.
* `dollar`: A string ending with one the strings '_USD_', '_CAD_', or '_AUD_'.
* `callno`: A string starting with two upper-case letters, followed by one or more digits, followed by an upper-case letter, followed by and ending with either two or four digits.

For example, `bcitid` should match the string `'A00123456 x '` but not `' A00123456'`.

#### Question 3

Write a function `foundat(p,s)` that returns a two-value tuple.  The first value is `True` if the string `s` matches the regular expression defined by the string `p`.  The second value is the zero-based index (location) of the first match of `p` in `s` or -1 if there was no match.

For example, `foundat('a',"bac")` would return `(True, 1)` while `foundat('x',"bac")` would return `(False, -1)`.

#### Question 4

Write a function `volsort(l)` that returns a sorted copy of the list of tuples `l`.  The tuples can have any number of elements.  The list should be sorted in increasing order of the product of the elements of the tuple.

The sort must be [stable](https://en.wikipedia.org/wiki/Sorting_algorithm#Stability) -- it must not change the order of items with the same key value.

For example `volsort([ (1,2,2), (-3,), (1,2), (2,1), (-1,2), (5,1,1,1)])` would return the list `[(-3,), (-1, 2), (1, 2), (2, 1), (1, 2, 2), (5, 1, 1, 1)]`.

#### Question 5

Write a class definition for a `resistor` type.  The constructor takes one argument: the resistance in ohms.  There are two methods: 
* `current(v)` returns the current through the resistor if the applied voltage is `v` and 
* `power(v)` returns the power dissipated by the resistor if the applied voltage if `v`

For example, 

    r1 = resistor(1e3)
    r1.current(3),r1.power(100)

would print `(0.003, 10.0)`

In [15]:
# lab validation code; do not modify
def labcheck(testing=0,ntest=10):
    '''
    Python exercise checking.
    Ed.Casas 2023-5-22
    Calls functions q<n>* and checks HMAC of return value[0].
    On mismatch prints return value[1] (function, arguments and return values).
    Setting testing=1 prints HMACs of correct results; paste into 'hashvalues'.
    Note:
    If q<n>* result not JSON-able, convert to string.
    Result order matters for comparison. Sort result if ordering not important.
    '''
    
    import base64, copy, hashlib, json, random, re, string, types 
    from random import randint
    import traceback
    
    # compare regex to strings that should/shouldn't match
    def checkre(pat,ok,nok):
        for s in ok:
            assert re.fullmatch(pat,s), \
                f"pattern '{pat}'\n did not match string '{s}'"
        for s in nok:
            assert not re.fullmatch(pat,s), \
                f"pattern '{pat}'\n matched string '{s}'"  
    
    # list of n words with nl letters from chars without repeats
    def randwords(n,chars=string.ascii_lowercase,nl=(2,5)):
        l = []
        while len(l)<n:
            w = ''.join([chars[randint(0,len(chars)-1)] for i in range(randint(*nl))])
            if w not in l:
                l.append(w)
        return l
    
    # convert sets to dicts and dict keys to strings so they can be sorted
    def orderkeys(o):
        if isinstance(o,set):
            return {str(k):None for k in o}
        if isinstance(o,dict):
            return {str(k):orderkeys(v) for k,v in o.items()}
        return o

    def Q1():
        f,a = birange,randint(1,4)
        oa = copy.deepcopy(a)
        r = list(birange(a))
        return r,f"birange({a}) returns {r}"
    

    def Q2():
        a = (   ( f"A{randint(1,9999_9999):08}",  f"A{randint(1,9999_9999):08}{chr(randint(32,64))}" ), 
                ( f"{chr(randint(32,64))}A{randint(1,9999_9999):08}", f"{chr(randint(32,64))}{chr(randint(32,64))}A{randint(1,9999_9999):08}" ) )
        checkre(bcitid,*a)
        
        a = (( f"${randint(0,9):1}.{randint(0,99):02}", f"${randint(0,9):1}.{randint(0,99):02}" ),
             (f"{randint(0,9):1}.{randint(0,99):02}",f"${randint(0,9):1}x{randint(0,99):02}",f"${randint(0,9):1}.{randint(0,999):03}"))
        checkre(amount,*a)
    
        currencies= [ "USD", "CAD", "AUD" ]
        a = ( ( f"{' '*randint(0,9)}{currencies[randint(0,2)]}", f"{' '*randint(0,9)}{currencies[randint(0,2)]}" ),
                ( f"{' '*randint(0,9)}{currencies[randint(0,2)]}{' '*randint(1,4)}", 
                 f"{currencies[randint(0,2)]}{chr(randint(32,64))*randint(1,4)}" ) )
        checkre(dollar,*a)
        
        cutter = f"{randint(0,99):02}" if randint(0,1) else f"{randint(0,9999):04}", f"{randint(0,99):02}" if randint(0,1) else f"{randint(0,9999):04}"
        a = ( ( f"{randwords(1,chars=string.ascii_uppercase,nl=(2,2))[0]}{randint(0,9999):0d}{randwords(1,chars=string.ascii_uppercase,nl=(1,1))[0]}{cutter[0]}",
            f"{randwords(1,chars=string.ascii_uppercase,nl=(2,2))[0]}{randint(0,999)}{randwords(1,chars=string.ascii_uppercase,nl=(1,1))[0]}{cutter[1]}" ), 
             ( f"{randwords(1,chars=string.ascii_lowercase,nl=(2,2))[0]}{randint(0,99)}{randwords(1,chars=string.ascii_uppercase,nl=(1,1))[0]}{cutter[0]}",
              f"{randwords(1,chars=string.ascii_uppercase,nl=(2,2))[0]}{randint(0,999)}{randwords(1,chars=string.ascii_uppercase,nl=(2,3))[0]}{cutter[1]}",
            f"{randwords(1,chars=string.ascii_uppercase,nl=(2,2))[0]}{randint(0,9999)}{randwords(1,chars=string.ascii_uppercase,nl=(1,1))[0]}{randint(0,999):03}" ))
        checkre(callno,*a)
        return 0,0


    def Q3():
        p = randwords(1)
        s = randwords(3)
        if randint(0,1):
            l = p+s
        else:
            l = s
        random.shuffle(l)
        p = p[0]
        s = ''.join(l)
        ops = copy.deepcopy((p,s))
        r = foundat(p,s)
        return r,f"foundat('{ops[0]}','{ops[1]}') returns {r}"
    
        
    def Q4():
        a = []
        for i in range(randint(2,5)):
            b = []
            for j in range(randint(1,4)):
                b.append(randint(-3,9))
            a.append(tuple(b))
                
        oa = copy.deepcopy(a)
        r = volsort(a)
        return r,f"volsort({oa}) returns {r}"

    import math
    def roundn(num, n):
        """
        Rounds a number to n significant figures.
        """
        if num != 0:
            return round(num, -int(math.floor(math.log10(abs(num)))) + (n - 1))
        else:
            return 0
            
    def Q5():
        r,v = randint(1,10_000),randint(1,100)
        orv = copy.deepcopy((r,v))
        o = resistor(r)
        a = roundn(o.current(v),4), roundn(o.power(v),4)
        return a,f"At voltage of {orv[1]}V a {orv[0]} ohm resistor has a current of {a[0]} A and dissipates {a[1]} W"
 
    hashvalues = '''
i4s2i4s2OQWU5Z0k5Z0kOQWU+Bnpi4s25Z0ki4s2
qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6qwW6
kiKdtlIhtlIhtlIhMId7I2rnv0LriMAwtlIh/N79
fTO2mV+HtLNUL3i7T3xUJqFwgBKeMZI2Hp8ToArA
CUMfG6/D2msNUYqx/VQRdhiB+WLK7YtVgjf8HEbg
'''.split()

    newhash = ''
    dsize = 3 # HMAC base64 digest size (bytes, use 3 or 6 for 4 or 8 char digests)
    dlen = ((dsize*8+5)//6+3)//4*4
           
    for n,f in [(n,f) for n,f in locals().items() if callable(f) and re.search(r'^[Qq]\d+.*',n)]:
        random.seed(n)      
        hashes = '0'*dlen*ntest if testing else hashvalues.pop(0)
        err = ''
        while hashes and not err:
            h, hashes = hashes[:dlen], hashes[dlen:] 
            try:
                v,s = f()
                b = json.dumps(orderkeys(v),sort_keys=True).encode()
                c = base64.b64encode(hashlib.blake2b(b,digest_size=dsize).digest()).decode()
                if testing:
                    print(s)
                    newhash += c
                else:
                    if c != h:
                        err = f"Wrong result for test {n}: {s} (HMAC={c} instead of {h})"
            except Exception as e:
                #traceback.print_exc()
                err = f"Error during test {n}: {e}"               
        if testing:
            newhash += '\n'
        else:
            print(err or f"Passed test {n}.")
            
    if testing:
        print(newhash)

labcheck(0)